<h1>Using LightGBM Classifier on credit card default data. </h1>

This notebook explores an application of the LightGBM package by Microsoft with a clean dataset on credit card defaults. Since we are trying to predict if a person is defaulting or not, we will want to use binary classification. This notebook also explores early stopping, is a form of regularization used to avoid overfitting when training a learner with an iterative method, such as gradient descent. Such methods update the learner so as to make it better fit the training data with each iteration. 


Dataset source: https://archive.ics.uci.edu/ml/datasets/default+of+credit+card+clients. 

In [143]:
import pandas as pd
from sklearn.cross_validation import train_test_split
import lightgbm as lgb
from sklearn.model_selection import GridSearchCV
import matplotlib.pyplot as plt
from sklearn.metrics import auc, accuracy_score, roc_auc_score

In [127]:
data = pd.read_excel('ccdata.xls', header = 1)

In [126]:
data.head()

LIMIT_BAL  SEX  EDUCATION  MARRIAGE  AGE  PAY_0  PAY_2  PAY_3  PAY_4  \
0      20000    2          2         1   24      2      2     -1     -1   
1     120000    2          2         2   26     -1      2      0      0   
2      90000    2          2         2   34      0      0      0      0   
3      50000    2          2         1   37      0      0      0      0   
4      50000    1          2         1   57     -1      0     -1      0   

   PAY_5             ...              BILL_AMT4  BILL_AMT5  BILL_AMT6  \
0     -2             ...                      0          0          0   
1      0             ...                   3272       3455       3261   
2      0             ...                  14331      14948      15549   
3      0             ...                  28314      28959      29547   
4      0             ...                  20940      19146      19131   

   PAY_AMT1  PAY_AMT2  PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  \
0         0       689         0         0         0         0   
1         0      1000      1000      1000         0      2000   
2      1518      1500      1000      1000      1000      5000   
3      2000      2019      1200      1100      1069      1000   
4      2000     36681     10000      9000       689       679   

   default payment next month  
0                           1  
1                           1  
2                           0  
3                           0  
4                           0  

[5 rows x 24 columns]

This research employed a binary variable, default payment (Yes = 1, No = 0), as the response variable. This study reviewed the literature and used the following 23 variables as explanatory variables:
- X1: Amount of the given credit (NT dollar): it includes both the individual consumer credit and his/her family (supplementary) credit.
- X2: Gender (1 = male; 2 = female).
- X3: Education (1 = graduate school; 2 = university; 3 = high school; 4 = others).
- X4: Marital status (1 = married; 2 = single; 3 = others).
- X5: Age (year).
- X6 - X11: History of past payment. We tracked the past monthly payment records (from April to September, 2005) as follows: X6 = the repayment status in September, 2005; X7 = the repayment status in August, 2005; . . .;X11 = the repayment status in April, 2005. The measurement scale for the repayment status is: -1 = pay duly; 1 = payment delay for one month; 2 = payment delay for two months; . . .; 8 = payment delay for eight months; 9 = payment delay for nine months and above.
- X12-X17: Amount of bill statement (NT dollar). X12 = amount of bill statement in September, 2005; X13 = amount of bill statement in August, 2005; . . .; X17 = amount of bill statement in April, 2005.
- X18-X23: Amount of previous payment (NT dollar). X18 = amount paid in September, 2005; X19 = amount paid in August, 2005; . . .;X23 = amount paid in April, 2005.


In [128]:
data.drop('ID', axis = 1, inplace = True)

In [129]:
data.isnull().sum().sort_values(ascending=False)

default payment next month    0
PAY_AMT6                      0
SEX                           0
EDUCATION                     0
MARRIAGE                      0
AGE                           0
PAY_0                         0
PAY_2                         0
PAY_3                         0
PAY_4                         0
PAY_5                         0
PAY_6                         0
BILL_AMT1                     0
BILL_AMT2                     0
BILL_AMT3                     0
BILL_AMT4                     0
BILL_AMT5                     0
BILL_AMT6                     0
PAY_AMT1                      0
PAY_AMT2                      0
PAY_AMT3                      0
PAY_AMT4                      0
PAY_AMT5                      0
LIMIT_BAL                     0
dtype: int64

In [130]:
X = data.drop(['default payment next month'], axis=1)
y = data['default payment next month']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=20)

<h2>LightGBM classifier hyperparameter optimization via scikit-learn's GridSearchCV</h2>

In [131]:
estimator = lgb.LGBMClassifier(objective='binary', class_weight = 'is_unbalance')
param_grid = {
    'n_estimators' : [x for x in range(10, 60)],
    'learning_rate' : [0.05, 0.1, 0.15, 0.2, 0.25],
    'num_leaves': [x for x in range(30, 70, 10)],
    'metric': ('l1', 'l2')
}
gridsearch = GridSearchCV(estimator, param_grid)

gridsearch.fit(X_train, y_train,
        eval_set=[(X_test, y_test)],
        eval_metric=['auc', 'binary_logloss'],
early_stopping_rounds=5)

print('Best parameters found by grid search are:', gridsearch.best_params_)

[1]	valid_0's binary_logloss: 0.670883	valid_0's auc: 0.768968
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650796	valid_0's auc: 0.775794
[3]	valid_0's binary_logloss: 0.632654	valid_0's auc: 0.775311
[4]	valid_0's binary_logloss: 0.616172	valid_0's auc: 0.774969
[5]	valid_0's binary_logloss: 0.601105	valid_0's auc: 0.776734
[6]	valid_0's binary_logloss: 0.587362	valid_0's auc: 0.77823
[7]	valid_0's binary_logloss: 0.574735	valid_0's auc: 0.778346
[8]	valid_0's binary_logloss: 0.56314	valid_0's auc: 0.778812
[9]	valid_0's binary_logloss: 0.552518	valid_0's auc: 0.779257
[10]	valid_0's binary_logloss: 0.542948	valid_0's auc: 0.778929
[1]	valid_0's binary_logloss: 0.670681	valid_0's auc: 0.767337
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650483	valid_0's auc: 0.770204
[3]	valid_0's binary_logloss: 0.632114	valid_0's auc: 0.770218
[4]	valid_0's binary_logloss: 0.615477	valid_0's auc: 0.7738

[1]	valid_0's binary_logloss: 0.670883	valid_0's auc: 0.768968
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650796	valid_0's auc: 0.775794
[3]	valid_0's binary_logloss: 0.632654	valid_0's auc: 0.775311
[4]	valid_0's binary_logloss: 0.616172	valid_0's auc: 0.774969
[5]	valid_0's binary_logloss: 0.601105	valid_0's auc: 0.776734
[6]	valid_0's binary_logloss: 0.587362	valid_0's auc: 0.77823
[7]	valid_0's binary_logloss: 0.574735	valid_0's auc: 0.778346
[8]	valid_0's binary_logloss: 0.56314	valid_0's auc: 0.778812
[9]	valid_0's binary_logloss: 0.552518	valid_0's auc: 0.779257
[10]	valid_0's binary_logloss: 0.542948	valid_0's auc: 0.778929
[11]	valid_0's binary_logloss: 0.53409	valid_0's auc: 0.778722
[1]	valid_0's binary_logloss: 0.670681	valid_0's auc: 0.767337
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650483	valid_0's auc: 0.770204
[3]	valid_0's binary_logloss: 0.632114	valid_0's auc: 0.7702

[1]	valid_0's binary_logloss: 0.670883	valid_0's auc: 0.768968
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650796	valid_0's auc: 0.775794
[3]	valid_0's binary_logloss: 0.632654	valid_0's auc: 0.775311
[4]	valid_0's binary_logloss: 0.616172	valid_0's auc: 0.774969
[5]	valid_0's binary_logloss: 0.601105	valid_0's auc: 0.776734
[6]	valid_0's binary_logloss: 0.587362	valid_0's auc: 0.77823
[7]	valid_0's binary_logloss: 0.574735	valid_0's auc: 0.778346
[8]	valid_0's binary_logloss: 0.56314	valid_0's auc: 0.778812
[9]	valid_0's binary_logloss: 0.552518	valid_0's auc: 0.779257
[10]	valid_0's binary_logloss: 0.542948	valid_0's auc: 0.778929
[11]	valid_0's binary_logloss: 0.53409	valid_0's auc: 0.778722
[12]	valid_0's binary_logloss: 0.525887	valid_0's auc: 0.779329
[1]	valid_0's binary_logloss: 0.670681	valid_0's auc: 0.767337
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650483	valid_0's auc: 0.770

[1]	valid_0's binary_logloss: 0.670683	valid_0's auc: 0.766158
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650569	valid_0's auc: 0.767837
[3]	valid_0's binary_logloss: 0.63221	valid_0's auc: 0.773578
[4]	valid_0's binary_logloss: 0.615431	valid_0's auc: 0.776246
[5]	valid_0's binary_logloss: 0.600439	valid_0's auc: 0.776155
[6]	valid_0's binary_logloss: 0.58662	valid_0's auc: 0.777804
[7]	valid_0's binary_logloss: 0.574013	valid_0's auc: 0.77742
[8]	valid_0's binary_logloss: 0.562501	valid_0's auc: 0.777699
[9]	valid_0's binary_logloss: 0.551753	valid_0's auc: 0.778528
[10]	valid_0's binary_logloss: 0.541956	valid_0's auc: 0.778748
[11]	valid_0's binary_logloss: 0.533147	valid_0's auc: 0.778306
[12]	valid_0's binary_logloss: 0.524912	valid_0's auc: 0.778437
[1]	valid_0's binary_logloss: 0.670883	valid_0's auc: 0.768968
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650796	valid_0's auc: 0.775

[13]	valid_0's binary_logloss: 0.518029	valid_0's auc: 0.778563
[1]	valid_0's binary_logloss: 0.670759	valid_0's auc: 0.766613
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.650659	valid_0's auc: 0.772682
[3]	valid_0's binary_logloss: 0.632321	valid_0's auc: 0.774071
[4]	valid_0's binary_logloss: 0.615794	valid_0's auc: 0.774116
[5]	valid_0's binary_logloss: 0.600606	valid_0's auc: 0.774562
[6]	valid_0's binary_logloss: 0.586772	valid_0's auc: 0.77583
[7]	valid_0's binary_logloss: 0.57409	valid_0's auc: 0.776971
[8]	valid_0's binary_logloss: 0.562667	valid_0's auc: 0.775986
[9]	valid_0's binary_logloss: 0.552037	valid_0's auc: 0.778009
[10]	valid_0's binary_logloss: 0.542317	valid_0's auc: 0.778141
[11]	valid_0's binary_logloss: 0.533295	valid_0's auc: 0.778918
[12]	valid_0's binary_logloss: 0.525093	valid_0's auc: 0.779103
[13]	valid_0's binary_logloss: 0.51756	valid_0's auc: 0.779294
[1]	valid_0's binary_logloss: 0.670734	valid_0's auc: 0

...

[14]	valid_0's binary_logloss: 0.432201	valid_0's auc: 0.778355
[15]	valid_0's binary_logloss: 0.432758	valid_0's auc: 0.778123
[16]	valid_0's binary_logloss: 0.433165	valid_0's auc: 0.777928
[17]	valid_0's binary_logloss: 0.434008	valid_0's auc: 0.776978
[18]	valid_0's binary_logloss: 0.434356	valid_0's auc: 0.776563
Early stopping, best iteration is:
[13]	valid_0's binary_logloss: 0.431786	valid_0's auc: 0.778893
[1]	valid_0's binary_logloss: 0.592696	valid_0's auc: 0.766158
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.534357	valid_0's auc: 0.773972
[3]	valid_0's binary_logloss: 0.497	valid_0's auc: 0.77836
[4]	valid_0's binary_logloss: 0.4732	valid_0's auc: 0.778734
[5]	valid_0's binary_logloss: 0.458468	valid_0's auc: 0.778368
[6]	valid_0's binary_logloss: 0.449125	valid_0's auc: 0.77765
[7]	valid_0's binary_logloss: 0.441997	valid_0's auc: 0.780182
[8]	valid_0's binary_logloss: 0.43785	valid_0's auc: 0.78045
[9]	valid_0's binary_logl

[1]	valid_0's binary_logloss: 0.59299	valid_0's auc: 0.764741
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.533421	valid_0's auc: 0.773855
[3]	valid_0's binary_logloss: 0.496271	valid_0's auc: 0.776704
[4]	valid_0's binary_logloss: 0.472387	valid_0's auc: 0.779072
[5]	valid_0's binary_logloss: 0.457624	valid_0's auc: 0.779077
[6]	valid_0's binary_logloss: 0.448798	valid_0's auc: 0.776563
[7]	valid_0's binary_logloss: 0.441843	valid_0's auc: 0.778414
[8]	valid_0's binary_logloss: 0.437881	valid_0's auc: 0.777332
[9]	valid_0's binary_logloss: 0.436098	valid_0's auc: 0.775438
[10]	valid_0's binary_logloss: 0.434231	valid_0's auc: 0.77644
Early stopping, best iteration is:
[5]	valid_0's binary_logloss: 0.457624	valid_0's auc: 0.779077
[1]	valid_0's binary_logloss: 0.593107	valid_0's auc: 0.760327
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.534312	valid_0's auc: 0.77281
[3]	valid_0's binary_loglo

[11]	valid_0's binary_logloss: 0.429919	valid_0's auc: 0.783949
[12]	valid_0's binary_logloss: 0.429233	valid_0's auc: 0.784126
[13]	valid_0's binary_logloss: 0.428945	valid_0's auc: 0.783728
[14]	valid_0's binary_logloss: 0.429102	valid_0's auc: 0.782939
[15]	valid_0's binary_logloss: 0.428894	valid_0's auc: 0.782968
[16]	valid_0's binary_logloss: 0.429262	valid_0's auc: 0.782694
[17]	valid_0's binary_logloss: 0.428928	valid_0's auc: 0.782825
Early stopping, best iteration is:
[12]	valid_0's binary_logloss: 0.429233	valid_0's auc: 0.784126
[1]	valid_0's binary_logloss: 0.593346	valid_0's auc: 0.767342
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.533886	valid_0's auc: 0.77553
[3]	valid_0's binary_logloss: 0.496836	valid_0's auc: 0.777774
[4]	valid_0's binary_logloss: 0.473291	valid_0's auc: 0.778408
[5]	valid_0's binary_logloss: 0.458374	valid_0's auc: 0.778925
[6]	valid_0's binary_logloss: 0.448406	valid_0's auc: 0.77921
[7]	valid_0's bi

[8]	valid_0's binary_logloss: 0.438147	valid_0's auc: 0.778112
[9]	valid_0's binary_logloss: 0.435703	valid_0's auc: 0.777156
[10]	valid_0's binary_logloss: 0.43397	valid_0's auc: 0.777801
[11]	valid_0's binary_logloss: 0.432393	valid_0's auc: 0.778407
[12]	valid_0's binary_logloss: 0.431904	valid_0's auc: 0.778536
[13]	valid_0's binary_logloss: 0.431786	valid_0's auc: 0.778893
[14]	valid_0's binary_logloss: 0.432201	valid_0's auc: 0.778355
[15]	valid_0's binary_logloss: 0.432758	valid_0's auc: 0.778123
[16]	valid_0's binary_logloss: 0.433165	valid_0's auc: 0.777928
[17]	valid_0's binary_logloss: 0.434008	valid_0's auc: 0.776978
[18]	valid_0's binary_logloss: 0.434356	valid_0's auc: 0.776563
Early stopping, best iteration is:
[13]	valid_0's binary_logloss: 0.431786	valid_0's auc: 0.778893
[1]	valid_0's binary_logloss: 0.592696	valid_0's auc: 0.766158
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.534357	valid_0's auc: 0.773972
[3]	valid_0's

[1]	valid_0's binary_logloss: 0.593041	valid_0's auc: 0.767052
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.533442	valid_0's auc: 0.77688
[3]	valid_0's binary_logloss: 0.496771	valid_0's auc: 0.778718
[4]	valid_0's binary_logloss: 0.473329	valid_0's auc: 0.778891
[5]	valid_0's binary_logloss: 0.457815	valid_0's auc: 0.779151
[6]	valid_0's binary_logloss: 0.44817	valid_0's auc: 0.77827
[7]	valid_0's binary_logloss: 0.442274	valid_0's auc: 0.777299
[8]	valid_0's binary_logloss: 0.437892	valid_0's auc: 0.778873
[9]	valid_0's binary_logloss: 0.435022	valid_0's auc: 0.779471
[10]	valid_0's binary_logloss: 0.433114	valid_0's auc: 0.780774
[11]	valid_0's binary_logloss: 0.432589	valid_0's auc: 0.779708
[12]	valid_0's binary_logloss: 0.432029	valid_0's auc: 0.779577
[13]	valid_0's binary_logloss: 0.431909	valid_0's auc: 0.779891
[14]	valid_0's binary_logloss: 0.431893	valid_0's auc: 0.779741
[15]	valid_0's binary_logloss: 0.431729	valid_0's auc: 

In [115]:
estimator = lgb.LGBMRegressor(objective='binary',
                       metric= 'l1' )
param_grid = {
    'n_estimators' : [18],
    'learning_rate' : [0.15],
    'num_leaves': [30],
    
}
gridsearch = GridSearchCV(estimator, param_grid)

gridsearch.fit(X_train, y_train,
        eval_set=[(X_test, y_test)],
        eval_metric=['auc', 'binary_logloss'],
early_stopping_rounds=5)

print('Best parameters found by grid search are:', gridsearch.best_params_)

[1]	valid_0's binary_logloss: 0.501446	valid_0's auc: 0.769006
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.482355	valid_0's auc: 0.772991
[3]	valid_0's binary_logloss: 0.46857	valid_0's auc: 0.775955
[4]	valid_0's binary_logloss: 0.459179	valid_0's auc: 0.776495
[5]	valid_0's binary_logloss: 0.452056	valid_0's auc: 0.777535
[6]	valid_0's binary_logloss: 0.446878	valid_0's auc: 0.777309
[7]	valid_0's binary_logloss: 0.442839	valid_0's auc: 0.777768
[8]	valid_0's binary_logloss: 0.439682	valid_0's auc: 0.778631
[9]	valid_0's binary_logloss: 0.437485	valid_0's auc: 0.777996
[10]	valid_0's binary_logloss: 0.436073	valid_0's auc: 0.777466
[11]	valid_0's binary_logloss: 0.434458	valid_0's auc: 0.778641
[12]	valid_0's binary_logloss: 0.433479	valid_0's auc: 0.778676
[13]	valid_0's binary_logloss: 0.432633	valid_0's auc: 0.778981
[14]	valid_0's binary_logloss: 0.432164	valid_0's auc: 0.779038
[15]	valid_0's binary_logloss: 0.431534	valid_0's auc

<h2>LightGBM Hyperparameters + early stopping</h2>

In [136]:

gbm = lgb.LGBMClassifier(objective='binary',
                        num_leaves=30,
                        metric = 'l1',
                        learning_rate=0.15,
                        n_estimators=18)
gbm.fit(X_train, y_train,
        eval_set=[(X_test, y_test)],
        eval_metric=['auc', 'binary_logloss'],
early_stopping_rounds=5)


[1]	valid_0's binary_logloss: 0.629723	valid_0's auc: 0.770333
Training until validation scores don't improve for 5 rounds.
[2]	valid_0's binary_logloss: 0.583069	valid_0's auc: 0.776794
[3]	valid_0's binary_logloss: 0.547984	valid_0's auc: 0.777552
[4]	valid_0's binary_logloss: 0.52095	valid_0's auc: 0.779434
[5]	valid_0's binary_logloss: 0.50039	valid_0's auc: 0.779279
[6]	valid_0's binary_logloss: 0.484201	valid_0's auc: 0.780934
[7]	valid_0's binary_logloss: 0.471693	valid_0's auc: 0.781571
[8]	valid_0's binary_logloss: 0.461774	valid_0's auc: 0.781893
[9]	valid_0's binary_logloss: 0.454251	valid_0's auc: 0.781763
[10]	valid_0's binary_logloss: 0.448386	valid_0's auc: 0.782052
[11]	valid_0's binary_logloss: 0.443613	valid_0's auc: 0.782899
[12]	valid_0's binary_logloss: 0.439931	valid_0's auc: 0.783576
[13]	valid_0's binary_logloss: 0.437049	valid_0's auc: 0.783893
[14]	valid_0's binary_logloss: 0.434972	valid_0's auc: 0.784209
[15]	valid_0's binary_logloss: 0.432931	valid_0's auc:

LGBMClassifier(boosting_type='gbdt', colsample_bytree=1.0, learning_rate=0.15,
        max_bin=255, max_depth=-1, metric='l1', min_child_samples=10,
        min_child_weight=5, min_split_gain=0.0, n_estimators=18, n_jobs=-1,
        num_leaves=30, objective='binary', random_state=0, reg_alpha=0.0,
        reg_lambda=0.0, silent=True, subsample=1.0,
        subsample_for_bin=50000, subsample_freq=1)

<h2>Feature Importances </h2>

In [137]:
ax = lgb.plot_importance(gbm, max_num_features=25)
plt.show()

In [138]:
y_pred = gbm.predict(X_test, num_iteration=gbm.best_iteration_)

In [144]:
print('The accuracy of prediction is:', accuracy_score(y_test, y_pred))
print('The roc_auc_score of prediction is:', roc_auc_score(y_test, y_pred))
print('The Null Acccuracy is:', max(y_test.mean(), 1 - y_test.mean()))

The accuracy of prediction is: 0.820666666667
The roc_auc_score of prediction is: 0.656823854494
The Null Acccuracy is: 0.7771666666666667
